In [42]:
from __future__ import absolute_import, division, print_function, unicode_literals
import tensorflow as tf
from tensorflow.keras import layers
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '2' 
import string
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import PIL
import random
import time
from pathlib import Path
from transformers import CLIPTokenizer, TFCLIPTextModel
import re
from IPython import display

In [43]:
gpus = tf.config.experimental.list_physical_devices('GPU')
if gpus:
    try:
        # Restrict TensorFlow to only use the first GPU
        tf.config.experimental.set_visible_devices(gpus[0], 'GPU')

        # Currently, memory growth needs to be the same across GPUs
        for gpu in gpus:
            tf.config.experimental.set_memory_growth(gpu, True)
        logical_gpus = tf.config.experimental.list_logical_devices('GPU')
        print(len(gpus), "Physical GPUs,", len(logical_gpus), "Logical GPUs")
    except RuntimeError as e:
        # Memory growth must be set before GPUs have been initialized
        print(e)

1 Physical GPUs, 1 Logical GPUs


In [44]:
data_path = './dataset'
df = pd.read_pickle(data_path + '/text2ImgData.pkl')
num_training_sample = len(df)
n_images_train = num_training_sample
print('There are %d image in training data' % (n_images_train))

There are 7370 image in training data


In [45]:
print(df['Captions'])

ID
6734    [[9, 2, 17, 9, 1, 6, 14, 13, 18, 3, 41, 8, 11,...
6736    [[4, 1, 5, 12, 2, 3, 11, 31, 28, 68, 106, 132,...
6737    [[9, 2, 27, 4, 1, 6, 14, 7, 12, 19, 5427, 5427...
6738    [[9, 1, 5, 8, 54, 16, 38, 7, 12, 116, 325, 3, ...
6739    [[4, 12, 1, 5, 29, 11, 19, 7, 26, 70, 5427, 54...
                              ...                        
8043    [[4, 1, 5, 2, 10, 6, 20, 3, 11, 7, 79, 5427, 5...
8044    [[8, 369, 403, 1, 7, 8, 71, 103, 3, 8, 21, 268...
8045    [[4, 1, 15, 14, 3, 11, 13, 18, 7, 2, 10, 6, 10...
8046    [[4, 1, 5, 2, 10, 6, 20, 7, 32, 79, 5427, 5427...
8047    [[4, 1, 5, 2, 10, 6, 11, 7, 22, 103, 5427, 542...
Name: Captions, Length: 7370, dtype: object


In [46]:
id2word_dict = dict(np.load('./dictionary/id2Word.npy'))

# Function to convert ids to words for one caption
def decode_caption(caption_id_list):
    return ' '.join([id2word_dict[str(id)] for id in caption_id_list if id2word_dict[str(id)] != '' and id2word_dict[str(id)] != '<PAD>' and id2word_dict[str(id)] != '<RARE>'])

# Each df['Captions'][i] is a list of 1-10 captions, each caption is a list of 20 word ids
# Decode all captions
all_captions_in_english = []
for caption_group in df['Captions']:
    english_captions = [decode_caption(caption) for caption in caption_group]
    all_captions_in_english.append(english_captions)

# Optionally: replace the captions in the dataframe
df['EnglishCaptions'] = all_captions_in_english

In [47]:
print(df['EnglishCaptions'])

ID
6734    [the petals of the flower are pink in color an...
6736    [this flower has white petals and yellow pisti...
6737    [the petals on this flower are pink with white...
6738    [the flower has a smooth purple petal with whi...
6739    [this white flower has bright yellow stamen wi...
                              ...                        
8043    [this flower has petals that are red and yello...
8044    [a tan pedaled flower with a black dots and a ...
8045    [this flower is pink and yellow in color with ...
8046    [this flower has petals that are red with dark...
8047    [this flower has petals that are yellow with o...
Name: EnglishCaptions, Length: 7370, dtype: object


In [48]:
i = 0
for group in df['EnglishCaptions']:
    i += 1
    print(f'Image {i} captions:')
    for caption in group:
        print(caption)

Image 1 captions:
the petals of the flower are pink in color and have a yellow center
this flower is pink and white in color with petals that are multi colored
the purple petals have shades of white with white anther and filament
this flower has large pink petals and a white stigma in the center
this flower has petals that are pink and has a yellow stamen
a flower with short and wide petals that is light purple
this flower has small pink petals with a yellow center
this flower has large rounded pink petals with curved edges and purple veins
this flower has purple petals as well as a white stamen
Image 2 captions:
this flower has white petals and yellow pistil as its main features
this is a white flower with a yellow center and yellow anthers
the flower has petals that are pale pink and white with yellow stamen
this flower is white and pink in color with petals that have veins
this flower has very long yellow stamen and a large white petal around it
this flower has large white petals wi

In [49]:
# in this competition, you have to generate image in size 64x64x3
IMAGE_HEIGHT = 64
IMAGE_WIDTH = 64
IMAGE_CHANNEL = 3
IMAGE_SIZE_CROPPED = 48
model_name = "openai/clip-vit-base-patch32"
tokenizer = CLIPTokenizer.from_pretrained(model_name)

def training_data_generator(input_ids, image_path):
    # load in the image according to image path
    img = tf.io.read_file(image_path)
    img = tf.image.decode_image(img, channels=3)
    img = tf.image.convert_image_dtype(img, tf.float32)
    img.set_shape([None, None, 3])
    img = tf.image.resize(img, size=[IMAGE_HEIGHT, IMAGE_WIDTH])
    img.set_shape([IMAGE_HEIGHT, IMAGE_WIDTH, IMAGE_CHANNEL])

    distorted_image = tf.image.random_crop(img, [IMAGE_SIZE_CROPPED,IMAGE_SIZE_CROPPED,IMAGE_CHANNEL])
    distorted_image = tf.image.resize(distorted_image, [IMAGE_HEIGHT, IMAGE_WIDTH])
    distorted_image = tf.image.random_flip_left_right(distorted_image)
    distorted_image = tf.image.random_brightness(distorted_image, max_delta=0.2)
    distorted_image = tf.image.random_contrast(distorted_image, lower=0.8, upper=1.2)
    # distorted_image = tf.image.per_image_standardization(distorted_image)
    # distorted_image = tf.clip_by_value(distorted_image, 0.0, 1.0)
    ## newly added
    distorted_image = tf.clip_by_value(distorted_image, 0.0, 1.0)
    distorted_image = (distorted_image - 0.5) * 2.0  # scale to [-1, 1]
    return distorted_image, input_ids

def dataset_generator(filenames, batch_size, data_generator):
    # load the training data into two NumPy arrays
    df = pd.read_pickle(filenames)
    captions = df['Captions'].values
    caption = []
    sentence = []
    # each image has 1 to 10 corresponding captions
    # we choose one of them randomly for training
    for i in range(len(captions)):
        temp = random.choice(captions[i])
        caption.append(temp)
        s = decode_caption(temp)
        sentence.append(s)
        
    model_name = "openai/clip-vit-base-patch32"
    tokenizer = CLIPTokenizer.from_pretrained(model_name)
    encodings = tokenizer(
        sentence, 
        padding="max_length", 
        truncation=True, 
        max_length=77,
        return_tensors="np"
    )
    input_ids = encodings['input_ids']
    
    image_path = df['ImagePath'].values
    
    dataset = tf.data.Dataset.from_tensor_slices((input_ids, image_path))
    dataset = dataset.map(data_generator, num_parallel_calls=tf.data.experimental.AUTOTUNE)
    dataset = dataset.shuffle(len(sentence)).batch(batch_size, drop_remainder=True)
    dataset = dataset.prefetch(buffer_size=tf.data.experimental.AUTOTUNE)

    return dataset

In [50]:
BATCH_SIZE = 64
dataset = dataset_generator(data_path + '/text2ImgData.pkl', BATCH_SIZE, training_data_generator)

<h2> text-encoder </h2>

In [51]:
# import tensorflow_hub as hub

# class BertTextEncoder(tf.keras.Model):
#     def __init__(self, hparas):
#         super(BertTextEncoder, self).__init__()
#         self.hparas = hparas
#         self.preprocessor = hub.KerasLayer("https://tfhub.dev/tensorflow/bert_en_uncased_preprocess/3")
#         self.encoder = hub.KerasLayer(
#     "https://tfhub.dev/tensorflow/bert_en_uncased_L-12_H-768_A-12/3",
#     trainable=False  
# )
        
#     def call(self, text):
#         # text: list of strings
#         text_inputs = self.preprocessor(text)
#         outputs = self.encoder(text_inputs)
#         return outputs['pooled_output']  # [batch_size, 768]


In [52]:
class ClipTextEncoder(tf.keras.Model):
    def __init__(self, hparas):
        super(ClipTextEncoder, self).__init__()
        model_name = "openai/clip-vit-base-patch32"
        self.encoder = TFCLIPTextModel.from_pretrained(model_name)
        self.encoder.trainable = False

    def call(self, input_ids):
        outputs = self.encoder(input_ids)
        return outputs.pooler_output

Generator


In [53]:
class Generator(tf.keras.Model):
    """
    Generate fake image based on given text(hidden representation) and noise z
    input: text and noise
    output: fake image with size 64*64*3
    """
    def __init__(self, hparas):
        super(Generator, self).__init__()
        self.flatten = tf.keras.layers.Flatten()
        # strengthen hidden size
        self.d1 = tf.keras.layers.Dense(hparas['DENSE_DIM']*2)
        self.bn1 = tf.keras.layers.BatchNormalization()
        self.d2 = tf.keras.layers.Dense(hparas['DENSE_DIM'])
        self.bn2 = tf.keras.layers.BatchNormalization()
        self.d3 = tf.keras.layers.Dense(hparas['DENSE_DIM'] // 2)
        self.d4 = tf.keras.layers.Dense(hparas['DENSE_DIM'] // 4)
        self.bn4 = tf.keras.layers.BatchNormalization()

        self.bn3 = tf.keras.layers.BatchNormalization()
        self.d_out = tf.keras.layers.Dense(64*64*3)
        
    def call(self, text, noise_z):
        x = self.flatten(text)
        x = self.d1(x)
        x = self.bn1(x)
        x = tf.nn.leaky_relu(x, alpha=0.2)

        x = self.d2(x)
        x = self.bn2(x)
        x = tf.nn.leaky_relu(x, alpha=0.2)

        x = self.d3(x)
        x = self.bn3(x)
        x = tf.nn.leaky_relu(x, alpha=0.2)

        x = self.d4(x)
        x = self.bn4(x)
        x = tf.nn.leaky_relu(x, alpha=0.2)

        # concatenate input text and random noise
        x = tf.concat([noise_z, x], axis=1)
        x = self.d_out(x)
        
        logits = tf.reshape(x, [-1, 64, 64, 3])
        output = tf.nn.tanh(logits)
        return logits, output


Discriminator


In [54]:
class Discriminator(tf.keras.Model):
    """
    Differentiate the real and fake image
    input: image and corresponding text
    output: labels, the real image should be 1, while the fake should be 0
    """
    def __init__(self, hparas):
        super(Discriminator, self).__init__()
        self.hparas = hparas
        self.flatten = tf.keras.layers.Flatten()
        self.d_text1 = tf.keras.layers.Dense(self.hparas['DENSE_DIM'])
        self.drop_text = tf.keras.layers.Dropout(0.3)
        self.bn_text1 = tf.keras.layers.BatchNormalization()
        self.d_text2 = tf.keras.layers.Dense(self.hparas['DENSE_DIM'])
        self.bn_text2 = tf.keras.layers.BatchNormalization()

        self.d_img1 = tf.keras.layers.Dense(self.hparas['DENSE_DIM'])
        self.drop_img = tf.keras.layers.Dropout(0.3)
        self.bn_img1 = tf.keras.layers.BatchNormalization()
        self.d_img2 = tf.keras.layers.Dense(self.hparas['DENSE_DIM'])
        self.bn_img2 = tf.keras.layers.BatchNormalization()

        self.d1 = tf.keras.layers.Dense(self.hparas['DENSE_DIM'])
        self.drop_joint = tf.keras.layers.Dropout(0.4)
        self.d2 = tf.keras.layers.Dense(1)

    def call(self, img, text, training=False):
        text = self.flatten(text)
        text = self.d_text1(text)
        text = tf.nn.leaky_relu(text, alpha=0.2)
        text = self.drop_text(text, training=training)

        img = self.flatten(img)
        img = self.d_img1(img)
        img = tf.nn.leaky_relu(img, alpha=0.2)
        img = self.drop_img(img, training=training)

        # concatenate image with paired text
        img_text = tf.concat([text, img], axis=1)
        img_text = self.d1(img_text)
        img_text = tf.nn.leaky_relu(img_text, alpha=0.2)
        img_text = self.drop_joint(img_text, training=training)

        logits = self.d2(img_text)
        output = tf.nn.sigmoid(logits)
        return logits, output


In [55]:
hparas = {
    'MAX_SEQ_LENGTH': 20,                     # maximum sequence length
    'Z_DIM': 512,                             # random noise z dimension
    'DENSE_DIM': 256,                         # number of neurons in dense layer
    'IMAGE_SIZE': [64, 64, 3],                # render image size
    'BATCH_SIZE': 64,
    'LR': 1e-4,
    'LR_DECAY': 0.5,
    'BETA_1': 0.5,
    'N_EPOCH': 500,                            # number of epoch for demo
    'N_SAMPLE': num_training_sample,          # size of training data
    'CHECKPOINTS_DIR': './checkpoints/demo',  # checkpoint path
    'PRINT_FREQ': 1                           # printing frequency of loss
}

In [56]:
text_encoder = ClipTextEncoder(hparas)
generator = Generator(hparas)
discriminator = Discriminator(hparas)

Some layers from the model checkpoint at openai/clip-vit-base-patch32 were not used when initializing TFCLIPTextModel: ['clip/vision_model/encoder/layers_._1/self_attn/k_proj/bias:0', 'clip/vision_model/encoder/layers_._9/self_attn/q_proj/kernel:0', 'clip/vision_model/encoder/layers_._8/self_attn/q_proj/bias:0', 'clip/vision_model/encoder/layers_._10/self_attn/q_proj/kernel:0', 'clip/vision_model/encoder/layers_._8/mlp/fc1/kernel:0', 'clip/vision_model/encoder/layers_._10/layer_norm2/gamma:0', 'clip/vision_model/encoder/layers_._11/layer_norm2/beta:0', 'clip/vision_model/encoder/layers_._1/layer_norm1/gamma:0', 'clip/vision_model/encoder/layers_._0/self_attn/v_proj/bias:0', 'clip/vision_model/encoder/layers_._6/self_attn/q_proj/bias:0', 'clip/vision_model/encoder/layers_._2/layer_norm2/beta:0', 'clip/vision_model/encoder/layers_._0/self_attn/k_proj/kernel:0', 'clip/vision_model/encoder/layers_._1/mlp/fc1/kernel:0', 'clip/vision_model/encoder/layers_._2/layer_norm1/gamma:0', 'clip/visio

Loss function and optimization

In [57]:
cross_entropy = tf.keras.losses.BinaryCrossentropy(from_logits=True)

In [58]:
def discriminator_loss(real_logits, fake_logits):
    # output value of real image should be 1
    real_loss = cross_entropy(tf.ones_like(real_logits) * 0.9, real_logits)
    # output value of fake image should be 0
    fake_loss = cross_entropy(tf.zeros_like(fake_logits), fake_logits)
    total_loss = real_loss + fake_loss
    return total_loss

def generator_loss(fake_output):
    # output value of fake image should be 0
    return cross_entropy(tf.ones_like(fake_output), fake_output)

In [59]:
generator_optimizer = tf.keras.optimizers.Adam(1e-3)
discriminator_optimizer = tf.keras.optimizers.Adam(1e-4)

In [ ]:
# one benefit of tf.train.Checkpoint() API is we can save everything seperately
checkpoint_dir = hparas['CHECKPOINTS_DIR']
checkpoint_prefix = os.path.join(checkpoint_dir, "ckpt")
checkpoint = tf.train.Checkpoint(generator_optimizer=generator_optimizer,
                                 discriminator_optimizer=disc3riminator_optimizer,
                                 text_encoder=text_encoder,
                                 generator=generator,
                                 discriminator=discriminator)

In [61]:
# newly added
steps_per_epoch = len(dataset) 
TOTAL_STEPS = int(steps_per_epoch * hparas['N_EPOCH'])
START_NOISE = 0.1        
print(f"(TOTAL_STEPS): {TOTAL_STEPS}")

(TOTAL_STEPS): 57500


In [62]:
@tf.function
def train_step(real_image, caption):
    text_embed = tf.stop_gradient(text_encoder(caption))
    # newly added
    current_step = tf.cast(discriminator_optimizer.iterations, tf.float32)
    decay_rate = tf.maximum(0.0, 1.0 - (current_step / TOTAL_STEPS))
    current_stddev = START_NOISE * decay_rate
    # newly added
    
    
    # Update D once # newly added (normalize noise)
    noise_d = tf.random.normal(shape=[hparas['BATCH_SIZE'], hparas['Z_DIM']])
    noise_d = tf.math.l2_normalize(noise_d, axis=1)
    with tf.GradientTape() as disc_tape:
        _, fake_image_d = generator(text_embed, noise_d, training=True)
        ## newly added
        img_noise = tf.random.normal(shape=tf.shape(real_image), mean=0.0, stddev=current_stddev)
        real_image = real_image + img_noise
        fake_image_d = fake_image_d + img_noise
        ## newly added
        real_logits, _ = discriminator(real_image, text_embed, training=True)
        fake_logits_d, _ = discriminator(fake_image_d, text_embed, training=True)
        d_loss = discriminator_loss(real_logits, fake_logits_d)

    grad_d = disc_tape.gradient(d_loss, discriminator.trainable_variables)
    discriminator_optimizer.apply_gradients(zip(grad_d, discriminator.trainable_variables))

    # Update G twice
    g_loss = 0.0
    for _ in tf.range(2):
        noise_g = tf.random.normal(shape=[hparas['BATCH_SIZE'], hparas['Z_DIM']])
        # newly added (normalize noise)
        noise_g = tf.math.l2_normalize(noise_g, axis=1)
        with tf.GradientTape() as gen_tape:
            _, fake_image_g = generator(text_embed, noise_g, training=True)
            ## newly added
            img_noise_g = tf.random.normal(shape=tf.shape(fake_image_g), mean=0.0, stddev=current_stddev)
            fake_image_g = fake_image_g + img_noise_g
            ## newly added
            
            fake_logits_g, _ = discriminator(fake_image_g, text_embed, training=True)
            curr_g_loss = generator_loss(fake_logits_g)

        grad_g = gen_tape.gradient(curr_g_loss, generator.trainable_variables)
        generator_optimizer.apply_gradients(zip(grad_g, generator.trainable_variables))
        g_loss += curr_g_loss

    g_loss = g_loss / 2.0 
    return g_loss, d_loss

In [63]:
@tf.function
def test_step(caption, noise):
    text_embed = text_encoder(caption)
    _, fake_image = generator(text_embed, noise)
    return fake_image

In [64]:
def merge(images, size):
    h, w = images.shape[1], images.shape[2]
    img = np.zeros((h * size[0], w * size[1], 3))
    for idx, image in enumerate(images):
        i = idx % size[1]
        j = idx // size[1]
        img[j*h:j*h+h, i*w:i*w+w, :] = image
    return img

def imsave(images, size, path):
    # getting the pixel values between [0, 1] to save it
    return plt.imsave(path, merge(images, size)*0.5 + 0.5)

def save_images(images, size, image_path):
    return imsave(images, size, image_path)

In [ ]:

def sample_generator(caption, batch_size):
    encodings = tokenizer(
        caption, 
        padding="max_length", 
        truncation=True, 
        max_length=77,
        return_tensors="np"
    )
    input_ids = encodings['input_ids']
    
    dataset = tf.data.Dataset.from_tensor_slices(input_ids)
    dataset = dataset.batch(batch_size)
    return dataset

In [66]:
ni = int(np.ceil(np.sqrt(hparas['BATCH_SIZE'])))
sample_size = hparas['BATCH_SIZE']
sample_seed = np.random.normal(loc=0.0, scale=1.0, size=(sample_size, hparas['Z_DIM'])).astype(np.float32)
# newly added (normalize noise)
sample_seed = sample_seed / np.linalg.norm(sample_seed, axis=1, keepdims=True)
sample_sentence = ["the flower shown has yellow anther red pistil and bright red petals."] * int(sample_size/ni) + \
                  ["this flower has petals that are yellow, white and purple and has dark lines"] * int(sample_size/ni) + \
                  ["the petals on this flower are white with a yellow center"] * int(sample_size/ni) + \
                  ["this flower has a lot of small round pink petals."] * int(sample_size/ni) + \
                  ["this flower is orange in color, and has petals that are ruffled and rounded."] * int(sample_size/ni) + \
                  ["the flower has yellow petals and the center of it is brown."] * int(sample_size/ni) + \
                  ["this flower has petals that are blue and white."] * int(sample_size/ni) +\
                  ["these white flowers have petals that start off white in color and end in a white towards the tips."] * int(sample_size/ni)

sample_sentence = sample_generator(sample_sentence, hparas['BATCH_SIZE'])

In [67]:
if not os.path.exists('samples/demo'):
    os.makedirs('samples/demo')

In [68]:
def train(dataset, epochs):
    # hidden state of RNN
    steps_per_epoch = int(hparas['N_SAMPLE']/hparas['BATCH_SIZE'])
    
    for epoch in range(hparas['N_EPOCH']):
        g_total_loss = 0
        d_total_loss = 0
        start = time.time()
        
        for image, caption in dataset:
            g_loss, d_loss = train_step(image, caption)
            g_total_loss += g_loss
            d_total_loss += d_loss
            
        time_tuple = time.localtime()
        time_string = time.strftime("%m/%d/%Y, %H:%M:%S", time_tuple)
            
        print("Epoch {}, gen_loss: {:.4f}, disc_loss: {:.4f}".format(epoch+1,
                                                                     g_total_loss/steps_per_epoch,
                                                                     d_total_loss/steps_per_epoch))
        print('Time for epoch {} is {:.4f} sec'.format(epoch+1, time.time()-start))
        
        # save the model
        if (epoch + 1) % 50 == 0:
            checkpoint.save(file_prefix = checkpoint_prefix)
        
        # visualization
        if (epoch + 1) % hparas['PRINT_FREQ'] == 0:
            for caption in sample_sentence:
                fake_image = test_step(caption, sample_seed)
            save_images(fake_image, [ni, ni], 'samples/demo/train_{:02d}.jpg'.format(epoch))

In [69]:
train(dataset, hparas['N_EPOCH'])

2025-11-27 01:56:20.924400: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:453] ShuffleDatasetV3:14: Filling up shuffle buffer (this may take a while): 2378 of 7370
2025-11-27 01:56:30.922683: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:453] ShuffleDatasetV3:14: Filling up shuffle buffer (this may take a while): 5105 of 7370
2025-11-27 01:56:39.763751: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:483] Shuffle buffer filled.
/home/yoyusamuel/hw8/.venv/lib/python3.10/site-packages/keras/src/layers/layer.py:421: UserWarning: `build()` was called on layer 'discriminator_1', however the layer does not have a `build()` method implemented and it looks like it has unbuilt state. This will cause the layer to be marked as built, despite not being actually built, which may cause failures down the line. Make sure to implement a proper `build()` method.
  warnings.warn(
2025-11-27 01:57:25.103867: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborti

Epoch 1, gen_loss: 3.1186, disc_loss: 2.9941
Time for epoch 1 is 74.3027 sec


2025-11-27 01:57:28.380049: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence


Epoch 2, gen_loss: 2.5646, disc_loss: 1.8305
Time for epoch 2 is 28.8121 sec


2025-11-27 01:57:57.658683: I tensorflow/core/framework/local_rendezvous.cc:407] Local rendezvous is aborting with status: OUT_OF_RANGE: End of sequence
2025-11-27 01:58:07.897245: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:453] ShuffleDatasetV3:14: Filling up shuffle buffer (this may take a while): 7197 of 7370
2025-11-27 01:58:08.108327: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:483] Shuffle buffer filled.


...

Epoch 439, gen_loss: 0.9209, disc_loss: 1.3295
Time for epoch 439 is 33.5709 sec


2025-11-27 05:44:24.466242: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:453] ShuffleDatasetV3:14: Filling up shuffle buffer (this may take a while): 5882 of 7370
2025-11-27 05:44:26.882205: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:483] Shuffle buffer filled.


Epoch 440, gen_loss: 0.9339, disc_loss: 1.3143
Time for epoch 440 is 32.2880 sec
Epoch 441, gen_loss: 0.9521, disc_loss: 1.3202
Time for epoch 441 is 28.7738 sec
Epoch 442, gen_loss: 0.9226, disc_loss: 1.3505
Time for epoch 442 is 28.8128 sec
Epoch 443, gen_loss: 0.9141, disc_loss: 1.3354
Time for epoch 443 is 28.6800 sec


2025-11-27 05:46:24.036129: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:453] ShuffleDatasetV3:14: Filling up shuffle buffer (this may take a while): 7245 of 7370
2025-11-27 05:46:24.176743: I tensorflow/core/kernels/data/shuffle_dataset_op.cc:483] Shuffle buffer filled.


Epoch 444, gen_loss: 0.9403, disc_loss: 1.3391
Time for epoch 444 is 29.4848 sec
Epoch 445, gen_loss: 0.9370, disc_loss: 1.3363
Time for epoch 445 is 40.9719 sec
Epoch 446, gen_loss: 0.9218, disc_loss: 1.3419
Time for epoch 446 is 29.7914 sec
Epoch 447, gen_loss: 0.9386, disc_loss: 1.3308
Time for epoch 447 is 29.2597 sec
Epoch 448, gen_loss: 0.9303, disc_loss: 1.3181
Time for epoch 448 is 29.1802 sec
Epoch 449, gen_loss: 0.9518, disc_loss: 1.3463
Time for epoch 449 is 29.1279 sec
Epoch 450, gen_loss: 0.9375, disc_loss: 1.3349
Time for epoch 450 is 28.6386 sec
Epoch 451, gen_loss: 0.9340, disc_loss: 1.3416
Time for epoch 451 is 29.1675 sec
Epoch 452, gen_loss: 0.9197, disc_loss: 1.3325
Time for epoch 452 is 29.0619 sec
Epoch 453, gen_loss: 0.9408, disc_loss: 1.3286
Time for epoch 453 is 29.7088 sec
Epoch 454, gen_loss: 0.9193, disc_loss: 1.3482
Time for epoch 454 is 29.3770 sec
Epoch 455, gen_loss: 0.9138, disc_loss: 1.3355
Time for epoch 455 is 29.3189 sec
Epoch 456, gen_loss: 0.9093,

In [70]:

def testing_data_generator(caption, index):
    caption = tf.cast(caption, tf.float32)
    return caption, index

def testing_dataset_generator(batch_size, data_generator):
    data = pd.read_pickle('./dataset/testData.pkl')
    captions = data['Captions'].values
    caption = []
    sentence = []
    for i in range(len(captions)):
        temp = captions[i]
        caption.append(temp)
        s = decode_caption(temp)
        sentence.append(s)
    captions = np.asarray(sentence)
    index = np.asarray(data['ID'].values)

    dataset = tf.data.Dataset.from_tensor_slices((captions, index))
    dataset = dataset.batch(batch_size, drop_remainder=False)
    return dataset
    


In [71]:
testing_dataset = testing_dataset_generator(hparas['BATCH_SIZE'], testing_data_generator)

In [72]:
data = pd.read_pickle('./dataset/testData.pkl')
captions = data['Captions'].values

NUM_TEST = len(captions)
EPOCH_TEST = int(NUM_TEST / hparas['BATCH_SIZE'])

In [73]:
if not os.path.exists('./inference/demo'):
    os.makedirs('./inference/demo')

In [85]:
def inference(dataset):
    sample_size = hparas['BATCH_SIZE']
    sample_seed = np.random.normal(loc=0.0, scale=1.0, size=(sample_size, hparas['Z_DIM'])).astype(np.float32)
    # newly added (normalize noise)
    sample_seed = sample_seed / np.linalg.norm(sample_seed, axis=1, keepdims=True)
    step = 0
    start = time.time()
    for captions, idx in dataset:
        if step > EPOCH_TEST:
            break
        
        captions_list = [c.decode('utf-8') for c in captions.numpy()]
        encodings = tokenizer(
            captions_list, 
            padding="max_length", 
            truncation=True, 
            max_length=77, 
            return_tensors="tf"
        )
        input_ids = encodings['input_ids']
        current_batch_size = tf.shape(input_ids)[0]
        noise = tf.random.normal(shape=(current_batch_size, hparas['Z_DIM']))
        noise = tf.math.l2_normalize(noise, axis=1)
        fake_image = test_step(input_ids, noise)
        step += 1
        current_batch_size = fake_image.shape[0]
        for i in range(current_batch_size):
            plt.imsave('./inference/demo/inference_{:04d}.jpg'.format(idx[i]), fake_image[i].numpy()*0.5 + 0.5)
            
    print('Time for inference is {:.4f} sec'.format(time.time()-start))

In [86]:
latest_ckpt = tf.train.latest_checkpoint(checkpoint_dir)
print("Restoring from:", latest_ckpt)
checkpoint.restore(latest_ckpt)

Restoring from: ./checkpoints/demo/ckpt-10


In [87]:
inference(testing_dataset)

Time for inference is 23.8074 sec
